In [1]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
from coil_geometry import create_coil_geometry
import numpy as np 

In [2]:
try:
    import webgui_jupyter_widgets
    from packaging.version import parse
    assert parse(webgui_jupyter_widgets.__version__) >= parse("0.2.18")
    print('Everything good!')
except:
    print("\x1b[31mYou need to update webgui_jupyter_widgets by running: \x1b[0m\npython3 -m pip install --upgrade webgui_jupyter_widgets")

Everything good!


In [3]:
nwindings = 6  # Number of windings
wireradius = 0.001  # Radius of the wire
coilradius = 0.01  # Radius of the coil

# Geometrie laden
geo, _ = create_coil_geometry(nwindings, wireradius, coilradius)

In [4]:
mesh = Mesh(
    geo.GenerateMesh()
)
mesh.Curve(1) 

In [5]:
Draw(mesh);

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

In [6]:
print("Materialien im Mesh:", mesh.GetMaterials())
print("Randbedingungen im Mesh:", mesh.GetBoundaries())

Materialien im Mesh: ('coil', 'air')
Randbedingungen im Mesh: ('out', 'coilbnd', 'in', 'outer', 'outer', 'outer', 'outer', 'outer', 'outer')


In [7]:
# Konstanten
mu = 4 * pi * 1e-7      # Magnetische Feldkonstante (S.2)
sigma_coil = 5.87e7     # Leitfähigkeit Kupfer (S.11)
sigma_air = 0           # Leitfähigkeit Luft
k = 0.1                 # Regularisierungfaktor
i_c = 500               # Strom

# Geometrische Parameter
A_c = pi * wireradius**2  
r = sqrt(x**2 + y**2 + z**2)

# Stromdichte j_c gemäß Aufgabenstellung
j_c = CoefficientFunction((
    (nwindings * i_c / A_c) * y / r,
    -(nwindings * i_c / A_c) * x / r,
    0
))

In [8]:
# H(curl)-Raum definieren
order = 2
V = HCurl(mesh, order=order-1, nograds=True, dirichlet="outer")
u, v = V.TnT()
gfA = GridFunction(V)


# Bilinearform und Linearform
a = BilinearForm(V, symmetric=True)
a += (1/mu) * InnerProduct(curl(u), curl(v)) * dx
a += k * InnerProduct(u, v) * dx

# Preconditioner
pre = Preconditioner(a, "multigrid")

# Linearform: Stromdichte
f = LinearForm(V)
f += InnerProduct(j_c, v) * dx("coil")

# Assemble
with TaskManager():
    a.Assemble()
    f.Assemble()

hcurl smoothingblocks, SmoothingType = 2


In [9]:
# Grösse von Gleichungsystems Elemente überprüfen
print(f"Matrix size: {a.mat.height} x {a.mat.width}")
print(f"Vector size: {f.vec.size}")
print(f"Präkonditionierer-Matrixgröße: {pre.mat.height} x {pre.mat.width}")

Matrix size: 157322 x 157322
Vector size: 157322
Präkonditionierer-Matrixgröße: 157322 x 157322


In [10]:
# Lösen des Gleichungssystems mit CG-Verfahren und Präkonditionierer (krylovspace.CGSolver)
inv = krylovspace.CGSolver(a.mat, pre.mat, tol=1e-12, printrates = True)

with TaskManager():
    gfA.vec.data = inv * f.vec

CG iteration 1, residual = 120469.14048934622     
CG iteration 2, residual = 2331.3206639947607     
CG iteration 3, residual = 53.071782281650094     
CG iteration 4, residual = 21.32852592332521     
CG iteration 5, residual = 10.477961054054042     
CG iteration 6, residual = 6.2445214862398215     
CG iteration 7, residual = 1.7254278915880763     
CG iteration 8, residual = 0.7021862761168116     
CG iteration 9, residual = 0.8359538463897412     
CG iteration 10, residual = 0.7428827514329526     
CG iteration 11, residual = 2.439836275312528     
CG iteration 12, residual = 1.3850799355493395     
CG iteration 13, residual = 0.8092531480275623     
CG iteration 14, residual = 0.6298091825387568     
CG iteration 15, residual = 0.14924886742914142     
CG iteration 16, residual = 0.27830389792201526     
CG iteration 17, residual = 0.41584035674834885     
CG iteration 18, residual = 0.4479691325674436     
CG iteration 19, residual = 0.5965630784685834     
CG iteration 20, res

In [11]:
# Visualisierung
Draw(curl(gfA), mesh, "MagneticField")

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene

In [12]:
Draw(gfA, mesh, "VectorPotential", draw_surf=True, draw_vol=True)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene

In [13]:
# Calculate the residual manually
residual_vec = f.vec - a.mat * gfA.vec
residual_norm = residual_vec.Norm()
print(f"Residual norm: {residual_norm}")

Residual norm: 841.2579572897084


In [14]:
B = curl(gfA) 

In [15]:
# Feldlinien to be done 
yiB = np.linspace(-.005,.005,9)
XiB, YiB = np.meshgrid(yiB,yiB)
fieldlines = B._BuildFieldLines(mesh, np.array([XiB.flatten(),
    YiB.flatten(),np.zeros_like(XiB.flatten())]).T,
    num_fieldlines=10**3//5, randomized=False,
    length=1.,thickness=8e-4)
Draw (B, mesh.Materials('coil'), objects=[fieldlines],
      draw_surf=False,
      min=0, max=0.1,
      settings={"Objects": {"Edges": False, "Surface": True,
                            "Wireframe": False}})

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {'Objects': {'Edges': False, …

BaseWebGuiScene

In [100]:
import numpy as np

# Example points
points = [
    (.01, 0.01, 0.05),  # Point 1
    (0.0, 0.02, 0.0),  # Point 2
    (0.0, 0.0, 0.01),  # Point 3
]
#points = [(0.01,0.02,0.01)]
for x, y, z in points:
    try:
        val = B(mesh(x, y, z)) 
        print(f"Value at point ({x}, {y}, {z}): {val}")
    except TypeError as e:
        print(f"Error at point ({x}, {y}, {z}): {e}")

Value at point (0.01, 0.01, 0.05): (-0.004311948333021837, -0.001207601088715899, 0.0)
Value at point (0.0, 0.02, 0.0): (-0.0009353886730941276, -0.010756694122688083, 0.06517908573405175)
Value at point (0.0, 0.0, 0.01): (-0.015472976636597701, 0.009085773831262845, -0.44352358964084954)


In [71]:
B.Point[1]

AttributeError: 'ngsolve.comp.GridFunctionCoefficientFunction' object has no attribute 'Point'

In [70]:
import numpy as np
from ngsolve import Mesh

# Define the mesh and B field (assume already initialized)
# mesh = Mesh("geometry.vol")
# B = ...  # Coefficient function or field representing B

# Define sampling points (same as used in fieldlines)
yiB = np.linspace(-0.005, 0.005, 9)
XiB, YiB = np.meshgrid(yiB, yiB)
sampling_points = np.array(
    [XiB.flatten(), YiB.flatten(), np.zeros_like(XiB.flatten())]
).T

# Evaluate B at each point
B_values = []
for point in sampling_points:
    x, y, z = point
    B_vec = B(x, y, z)  # Evaluate B at (x, y, z)
    B_values.append(B_vec)

# Convert to a NumPy array
B_values = np.array(B_values)  # Shape: (num_points, 3)

# Save to a file
np.savetxt(
    "B_sampling.csv",
    np.hstack([sampling_points, B_values]),
    delimiter=",",
    header="x,y,z,Bx,By,Bz",
)

ValueError: all the input arrays must have same number of dimensions, but the array at index 0 has 2 dimension(s) and the array at index 1 has 1 dimension(s)

In [58]:
bb_region = mesh.BBBoundaries(".*")  # Select all co-dimension 3 boundaries (vertices)
for vertex in mesh.vertices:
    print(vertex.nr)  # Access vertex indices or other properties

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [66]:
from ngsolve import *

# Assuming 'mesh' is your NGSolve mesh
for vertex in mesh.vertices:
    coords = vertex.point  # Get the coordinates of the vertex
    print(f"Vertex {vertex.nr}: {coords}")
    val = B(mesh(coords))
    print("magnetic field at coord"+ str(val))

Vertex 0: (0.010000000000000014, 2.2490418815496183e-17, -0.0062)
magnetic field at coord[[-0.16710401 -0.04002929 -0.46892834]
 [ 0.00465424 -0.01530761 -0.8202569 ]
 [ 0.00627899 -0.01174545 -0.93557358]]
Vertex 1: (0.009001831695215807, 3.6349960099299956e-05, 0.00724836027009205)
magnetic field at coord[[-0.05513382 -0.02887917 -1.11638498]
 [ 0.00465424 -0.01530761 -0.8202569 ]
 [ 0.00539398 -0.02529144 -0.9777813 ]]
Vertex 2: (-0.05, -0.05, 0.05)
magnetic field at coord[[ 0.         -0.00051679  0.01166434]
 [ 0.         -0.00051679  0.01166434]
 [ 0.         -0.00068316  0.01149218]]
Vertex 3: (-0.05, -0.05, -0.05)
magnetic field at coord[[ 0.         -0.00051679  0.01166434]
 [ 0.         -0.00051679  0.01166434]
 [ 0.         -0.00051679  0.01166434]]
Vertex 4: (-0.05, 0.05, 0.05)
magnetic field at coord[[ 0.         -0.00051679  0.01166434]
 [ 0.         -0.00068316  0.01149218]
 [ 0.         -0.00068316  0.01149218]]
Vertex 5: (-0.05, 0.05, -0.05)
magnetic field at coord[[ 0

In [103]:
import numpy as np

point = np.array([0.01, 0, 0])  # Single point as a 1D array
val = B(mesh(point))
print(val)
type(val)

[[-0.16710401 -0.04002929 -0.46892834]
 [ 0.00465424 -0.01530761 -0.8202569 ]
 [ 0.00465424 -0.01530761 -0.8202569 ]]


numpy.ndarray

In [28]:
from netgen.csg import Pnt

# Create the geometry
geo, crosssection = create_coil_geometry(nwindings=6, wireradius=0.001, coilradius=0.01)

# Access the bounding box from the Netgen representation
bb_min = Pnt(*geo.Box().PMin())
bb_max = Pnt(*geo.Box().PMax())

# Extract ranges for each dimension
x_range = (bb_min.X(), bb_max.X())
y_range = (bb_min.Y(), bb_max.Y())
z_range = (bb_min.Z(), bb_max.Z())

# Print the results
print("Bounding Box (Min):", (bb_min.X(), bb_min.Y(), bb_min.Z()))
print("Bounding Box (Max):", (bb_max.X(), bb_max.Y(), bb_max.Z()))
print("X Range:", x_range)
print("Y Range:", y_range)
print("Z Range:", z_range)

AttributeError: 'netgen.libngpy._NgOCC.OCCGeometry' object has no attribute 'Box'

In [43]:
print(B)
print(type(B))

coef N6ngcomp31GridFunctionCoefficientFunctionE, real, dim=3

<class 'ngsolve.comp.GridFunctionCoefficientFunction'>


In [50]:
import numpy as np
import pandas as pd

# Define the fieldline parameters
yiB = np.linspace(-0.005, 0.005, 9)
XiB, YiB = np.meshgrid(yiB, yiB)

# Generate fieldlines
fieldlines = B._BuildFieldLines(
    mesh,
    np.array([XiB.flatten(), YiB.flatten(), np.zeros_like(XiB.flatten())]).T,
    num_fieldlines=10**3 // 5,
    randomized=False,
    length=1.0,
    thickness=8e-4,
)

# Collect fieldline data
fieldline_data = []
for line in fieldlines:
    for point in line:
        position = point[0:3]  # x, y, z coordinates
        field_value = B(point)  # Evaluate magnetic field at this point
        fieldline_data.append((*position, *field_value))

# Convert to a structured format (DataFrame)
df = pd.DataFrame(fieldline_data, columns=["x", "y", "z", "Bx", "By", "Bz"])

# Save to a CSV file
df.to_csv("fieldline_data.csv", index=False)
print("Fieldline data saved to 'fieldline_data.csv'")

ImportError: C extension: None not built. If you want to import pandas from the source directory, you may need to run 'python setup.py build_ext' to build the C extensions first.

In [69]:
help(mesh.Contains(0,-0.05,0))
x, y, z = #1.0, 1.0, 0.0

# Check if the point is inside the mesh
is_inside = mesh.Contains(x, y, z)
print(f"Point ({x}, {y}, {z}) is inside the mesh: {is_inside}")

Help on bool object:

class bool(int)
 |  bool(x) -> bool
 |  
 |  Returns True when the argument x is true, False otherwise.
 |  The builtins True and False are the only two instances of the class bool.
 |  The class bool is a subclass of the class int, and cannot be subclassed.
 |  
 |  Method resolution order:
 |      bool
 |      int
 |      object
 |  
 |  Methods defined here:
 |  
 |  __and__(self, value, /)
 |      Return self&value.
 |  
 |  __or__(self, value, /)
 |      Return self|value.
 |  
 |  __rand__(self, value, /)
 |      Return value&self.
 |  
 |  __repr__(self, /)
 |      Return repr(self).
 |  
 |  __ror__(self, value, /)
 |      Return value|self.
 |  
 |  __rxor__(self, value, /)
 |      Return value^self.
 |  
 |  __xor__(self, value, /)
 |      Return self^value.
 |  
 |  ----------------------------------------------------------------------
 |  Static methods defined here:
 |  
 |  __new__(*args, **kwargs) from builtins.type
 |      Create and return a new o

In [107]:
#!/usr/bin/env python3
import numpy as np
import csv
from tqdm import tqdm

# Hier wird davon ausgegangen, dass mesh und B bereits definiert sind, z.B.:
# mesh.Contains(x, y, z) -> bool
# B(x, y, z) -> (Bx, By, Bz)

# Konfigurierbare Parameter
NUM_SAMPLES = 1000000
MIN_VAL = -0.05
MAX_VAL = 0.05
CSV_FILENAME = "results.csv"

# 1) Erzeuge eine Menge für eindeutige (x, y, z)-Koordinaten
points = set()

# 2) Erzeuge Zufallskoordinaten, bis mindestens NUM_SAMPLES zusammenkommen
while len(points) < NUM_SAMPLES:
    x = np.random.uniform(MIN_VAL, MAX_VAL)
    y = np.random.uniform(MIN_VAL, MAX_VAL)
    z = np.random.uniform(MIN_VAL, MAX_VAL)
    # Optionales Runden, um zu viele nah-beieinanderliegende Werte zu reduzieren:
    x, y, z = round(x, 5), round(y, 5), round(z, 5)
    points.add((x, y, z))

# 3) Werte B an den gültigen Punkten aus und sammle die Resultate
results = []

print("Starte Auswertung der Punkte ...")
for x, y, z in tqdm(points, desc="Evaluating points"):
    # Prüfe, ob das Mesh den Punkt enthält
    if mesh.Contains(x, y, z):
        try:
            bx, by, bz = B(mesh(x, y, z))  # ggf. anpassen, je nach Signatur
            results.append((x, y, z, bx, by, bz))
        except TypeError as e:
            print(f"TypeError bei Punkt ({x}, {y}, {z}): {e}")
        except Exception as e:
            print(f"Unerwarteter Fehler bei Punkt ({x}, {y}, {z}): {e}")
    # Falls das Mesh den Punkt nicht enthält: keine Aktion

# 4) Speichere die Ergebnisse in einer CSV-Datei
with open(CSV_FILENAME, mode="w", newline="") as f:
    writer = csv.writer(f)
    writer.writerow(["x", "y", "z", "Bx", "By", "Bz"])  # Header
    writer.writerows(results)

print(
    f"Fertig! {len(results)} Punkte wurden erfolgreich ausgewertet und in '{CSV_FILENAME}' gespeichert."
)

Starte Auswertung der Punkte ...


Evaluating points: 100%|██████████| 1000000/1000000 [00:36<00:00, 27444.08it/s]


Fertig! 1000000 Punkte wurden erfolgreich ausgewertet und in 'results.csv' gespeichert.
